In [1]:
import cv2 as cv
import numpy as np
import matplotlib.pyplot as plt
import copy
import os
import time
import csv

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [3]:
class cellpoint:
  frame: int
  id: int
  posx: int
  posy: int
  prev_point_missing: bool
  open_ending: bool

In [70]:
#Listing all the videos in a folder

AvailableVideos = os.listdir("/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Validisation data/01 Videos/AllControls/")
CellTypes = []
for CurrentVideo in AvailableVideos:
  splitted = CurrentVideo.split('.')
  CellTypes.append(splitted[0])
CellTypes.sort()
for CellType in CellTypes:
  print(CellType)

BIBF06_22
BIBF07_22
BIBF07_23
BIBF_01_1
BIBF_01_3
BIBF_01_7
BIBF_02_13
BIBF_02_20
BIBF_03_22
BIBF_03_24
BIBF_04_13
BIBF_04_19
BIBF_04_21
BRAF01_13
BRAF01_14
BRAF01_30
BRAF01_5
BRAF01_6
BRAF02_17
BRAF02_31
BRAF02_33
BRAF02_8
BRAF03_13
BRAF03_28
BRAF03_35
BRAF04_17
BRAF04_2
BRAF04_22
BRAF04_26
BRAF04_31
BRAF04_33
BRAF04_7
BRAF05_10
BRAF05_11
BRAF05_12
BRAF05_4
BRAF05_5
BRAF05_7
BRAF05_8
BRAF06_1
BRAF06_2
BRAF06_3
BRAF06_31
BRAF08_15
BRAF08_36
BRAF08_9
BRAF09_12
BRAF09_13
BRAF09_14
BRAF09_35
BRAF09_36
BRAF10_15
BRAF10_35
BRAF11_10
BRAF11_13
BRAF11_14
BRAF11_35
BRAF12_13
BRAF12_14
BRAF12_34
BRAF13_11
BRAF13_15
FAKinh01_12
FAKinh01_14
FAKinh01_4
FAKinh171010_1
FAKinh171010_16
FAKinh171010_2
FAKinh171010_6
FAKinh171010_8
FAKinh171010_9
MM05_19
MM05_20
MM05_22
MM05_24
T46_T47_drug01_20
T46_T47_drug01_21
T46_T47_drug01_4
T46_T47_drug01_5
T46_T47_drug02_20
T46_T47_drug02_5
T46_T47_siMVP_01_14
aktivin01_2
aktivin01_22
aktivin01_3
aktivin02_2
aktivin02_22
aktivin02_23
cldn4_02_19
cldn4_02_20
cldn

In [5]:
def DefineStartingAndEndingFrameOnHumanData(CellType, HumanDataFolder):
  HumanAnnotPath = HumanDataFolder+CellType+".path"
  HumanAnnotFile = open(HumanAnnotPath,"r") 
  HumanAnnotList = HumanAnnotFile.readlines()

  StartingFrame = -1
  EndingFrame = 0

  for row in HumanAnnotList:
    splitted = row.split(' ')
    if splitted[0].isdigit():
      CurrentFrame = int(splitted[2])
      if CurrentFrame<StartingFrame or StartingFrame == -1:
        StartingFrame = CurrentFrame
      if CurrentFrame>EndingFrame:
        EndingFrame = CurrentFrame

  return [StartingFrame,EndingFrame]

In [77]:
#Setting up parameters
#CellTypes = ['BIBF_01_7','aktivin01_2','aktivin01_3','hipox03_2','melanoma_GF01_11','zometa01_4']
inp_video_path = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Validisation data/01 Videos/AllControls/"
out_text_path = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Valid cell selector/outputs/"
HumanDataFolder = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Validisation data/02 Human Annotations/AllControls/"

FileNameModifier = "AllControlsInHumanRange"

MaxFrameNumber = -1

AcceptedWrongFrameRate = 0.3
AcceptedMaxCoverage = 0.5

Clocksize = [140,25]
StartFromStartingFrame = True
EndAtEndingFrame = True

In [79]:
# MAIN CODE

OutValidCells = open(out_text_path+"ValidCells"+FileNameModifier+'.txt','w')

ValidCellTypes = []

#Iterating through all the chosen cells
CellsAlreadyAnalysed = 0

for cell_name in CellTypes:
  print(cell_name +"\t"+str(CellsAlreadyAnalysed+1)+"/"+str(len(CellTypes)), end ="\t")
  #Setting up video reading

  cap = cv.VideoCapture(inp_video_path+cell_name+'.mpeg')
  ret, frame1 = cap.read()
  prvs = cv.cvtColor(frame1,cv.COLOR_BGR2GRAY)
  hsv = np.zeros_like(frame1)
  hsv[...,1] = 255

  #FRAME 2
  row=1

  #Video Write object
  frame_width=int(cap.get(3))
  frame_height=int(cap.get(4))

  #Setting up similar parameters as in case of the human annotation

  StartingFrame = 0
  EndingFrame = -1
  [HumanStartingFrame, HumanEndingFrame] = DefineStartingAndEndingFrameOnHumanData(cell_name, HumanDataFolder)
  if StartFromStartingFrame:
    StartingFrame = HumanStartingFrame
    #print("Starting Frame: "+np.str(StartingFrame))
  if EndAtEndingFrame:
    EndingFrame = HumanEndingFrame
    #print("Ending Frame: "+np.str(EndingFrame))

  #Starting the analysis

  FrameCounter = 0
  ret, frame2 = cap.read()

  ValidFrameList = [] # 0-Invalid 1-Valid

  #------------ Starting the run for the individual video ------------

  while(ret and (MaxFrameNumber == -1 or FrameCounter<MaxFrameNumber+StartingFrame)):
  
    next1 = cv.cvtColor(frame2,cv.COLOR_BGR2GRAY)

    if FrameCounter>=StartingFrame and (EndingFrame == -1 or FrameCounter<=EndingFrame):

      Timer = time.time()
      
      H,W = next1.shape
      
      #------------ Deciding validity ------------

      tresh = ((1-(next1 < 150)*(next1>100))*255).astype(np.uint8)  #band cut treshold
      tresh[H-Clocksize[1]:H,0:Clocksize[0]]=0
      
      closing_kernel = np.ones((15,15),np.uint8)
      
      closed = cv.morphologyEx(tresh, cv.MORPH_CLOSE, closing_kernel)
      medianed = cv.medianBlur(closed, 11)
      binarized = np.around(np.array((medianed/255).squeeze())).astype(int)

      if float(sum(sum(binarized)))/(H*W)>AcceptedMaxCoverage:
        ValidFrameList.append(0)
      else:
        ValidFrameList.append(1)

    FrameCounter+=1
    prvs = next1
    ret, frame2 = cap.read()

  if 1-sum(ValidFrameList)/len(ValidFrameList)<AcceptedWrongFrameRate:
    ValidCellTypes.append(cell_name)
    OutValidCells.write(cell_name+"\n")
    print("Valid")
  else:
    print("Invalid")

  cap.release()
  cv.destroyAllWindows()
  CellsAlreadyAnalysed+=1

OutValidCells.close()

print("Run finished sucessfully")
print("Rate of valid cells: " +str(len(ValidCellTypes))+"/"+str(len(CellTypes)))

BIBF06_22	1/391	Valid
BIBF07_22	2/391	Valid
BIBF07_23	3/391	Valid
BIBF_01_1	4/391	Valid
BIBF_01_3	5/391	Valid
BIBF_01_7	6/391	Valid
BIBF_02_13	7/391	Valid
BIBF_02_20	8/391	Invalid
BIBF_03_22	9/391	Valid
BIBF_03_24	10/391	Valid
BIBF_04_13	11/391	Valid
BIBF_04_19	12/391	Invalid
BIBF_04_21	13/391	Valid
BRAF01_13	14/391	Invalid
BRAF01_14	15/391	Invalid
BRAF01_30	16/391	Valid
BRAF01_5	17/391	Invalid
BRAF01_6	18/391	Invalid
BRAF02_17	19/391	Valid
BRAF02_31	20/391	Valid
BRAF02_33	21/391	Valid
BRAF02_8	22/391	Invalid
BRAF03_13	23/391	Invalid
BRAF03_28	24/391	Invalid
BRAF03_35	25/391	Valid
BRAF04_17	26/391	Valid
BRAF04_2	27/391	Invalid
BRAF04_22	28/391	Invalid
BRAF04_26	29/391	Valid
BRAF04_31	30/391	Valid
BRAF04_33	31/391	Valid
BRAF04_7	32/391	Invalid
BRAF05_10	33/391	Valid
BRAF05_11	34/391	Valid
BRAF05_12	35/391	Valid
BRAF05_4	36/391	Invalid
BRAF05_5	37/391	Invalid
BRAF05_7	38/391	Valid
BRAF05_8	39/391	Invalid
BRAF06_1	40/391	Valid
BRAF06_2	41/391	Valid
BRAF06_3	42/391	Invalid
BRAF06_31	43/391